In [292]:
%pip install -r requirements.txt -U -q

Note: you may need to restart the kernel to use updated packages.


# Read Dataset

The data has been massaged and saved as `county_records.csv`. This transposes the columns/rows in the Excel document and massages the column headers.

This also adds the `ID` and `fullName` standardization from the Newberry county data.

In [293]:
import pandas as pd

# read massaged CSV
df = pd.read_csv('county_records.csv', na_filter=False)
df.head()

ID     county burned published court_count1 court_count_2  \
0   vas_accomack   Accomack      0         2                          1   
1  vas_albemarle  Albemarle      1         1                              
2     vas_amelia     Amelia      0         2                          1   
3    vas_amherst    Amherst      0                                    1   
4    vas_augusta    Augusta      0                                    1   

    fullName  
0   ACCOMACK  
1  ALBEMARLE  
2     AMELIA  
3    AMHERST  
4    AUGUSTA

# Read GeoJSON

Read the GeoJSON file and convert to a `geopandas` dataframe.

Data was donloaded from Newberry County records and massaged a bit so that the `fullName` can be keyed to merge with the county data.

In [294]:
import geopandas as gpd

counties = gpd.read_file('massaged.geojson')
counties.head()

fullName  \
0                       GLOUCESTER   
1              FINCASTLE (extinct)   
2                NORFOLK (extinct)   
3  West Augusta District (extinct)   
4                          BEDFORD   

                                              change  \
0               [1651] GLOUCESTER created from YORK.   
1        FINCASTLE (extinct) created from BOTETOURT.   
2  NORFOLK (extinct) created from LOWER NORFOLK; ...   
3  West Augusta District (extinct) created by Vir...   
4       BEDFORD gained from ALBEMARLE and LUNENBURG.   

                                               dates  \
0  {'start': '1651-12-31T00:00:00Z', 'end': '1776...   
1  {'start': '1772-12-01T00:00:00Z', 'end': '1776...   
2  {'start': '1691-05-16T00:00:00Z', 'end': '1776...   
3  {'start': '1773-10-11T00:00:00Z', 'end': '1776...   
4  {'start': '1755-01-01T00:00:00Z', 'end': '1776...   

                                            geometry  
0  MULTIPOLYGON (((-76.27557 37.30574, -76.27869 ...  
1  MULTIPOLYGON (((-89.47247 36.51375, -89.48511 ...  
2  MULTIPOLYGON (((-76.37459 36.88549, -76.37656 ...  
3  MULTIPOLYGON (((-78.80811 40.72065, -78.86011 ...  
4  MULTIPOLYGON (((-79.43516 37.60388, -79.42851 ...

# Merge the datasets

Merge the two datasets by `fullName` and outer join.

In [295]:
merged = df.merge(counties, on='fullName', how='outer')

# # convert to GeoDataframe
data = gpd.GeoDataFrame(merged)
data.head()

ID     county burned published court_count1 court_count_2  \
0   vas_accomack   Accomack      0         2                          1   
1  vas_albemarle  Albemarle      1         1                              
2     vas_amelia     Amelia      0         2                          1   
3    vas_amherst    Amherst      0                                    1   
4    vas_augusta    Augusta      0                                    1   

    fullName                                             change  \
0   ACCOMACK          [1663] ACCOMACK created from NORTHAMPTON.   
1  ALBEMARLE  ALBEMARLE gained from LOUISA, lost to creation...   
2     AMELIA          AMELIA lost to creation of PRINCE EDWARD.   
3    AMHERST                    AMHERST created from ALBEMARLE.   
4    AUGUSTA  AUGUSTA lost to creation of West Augusta Distr...   

                                               dates  \
0  {'start': '1663-12-31T00:00:00Z', 'end': '1776...   
1  {'start': '1761-05-01T00:00:00Z', 'end': '1776...   
2  {'start': '1754-01-01T00:00:00Z', 'end': '1776...   
3  {'start': '1761-05-01T00:00:00Z', 'end': '1776...   
4  {'start': '1773-10-11T00:00:00Z', 'end': '1776...   

                                            geometry  
0  MULTIPOLYGON (((-75.81141 37.79399, -75.81149 ...  
1  MULTIPOLYGON (((-78.58292 38.25014, -78.36980 ...  
2  MULTIPOLYGON (((-77.96820 37.48573, -77.95902 ...  
3  MULTIPOLYGON (((-78.83921 38.04757, -78.69671 ...  
4  MULTIPOLYGON (((-79.92785 39.58906, -79.91059 ...

# Set Colors

Set colors that correspond to the `burn` column values.

In [296]:
# burn_colors = { '': '#00000000', '0': '#08AAD8', '1': '#73D0F2' }
burn_colors = { '': '', '0': '#dddddd', '1': '#cc0024' }
# publish_colors = { '': '#00000000', '0': '#FEF0E3', '1': '#F79768', '2': '#F26B28' }
publish_colors = { '': '#00000000', '0': '#dddddd', '1': '#7bb3d1', '2': '#016eae' }
# april_colors = { '': '#00000000', '0': '#FEF0E3', '1': '#F79768', '2': '#F26B28' }
# april_colors = { '': '#00000000', '0': '#F0DCDA', '1': '#E6B8B8', '2': '#DA9695' }
# may_colors = { '': '#00000000', '0': '#D4D6DC', '1': '#C3CCD7', '2': '#A0B5D2' }

april_colors = { '': '#00000000', '0': '#FEF1E4', '1': '#74D0F2', '2': '#0BABD9' }
may_colors = { '': '#00000000', '0': '#FEF1E4', '1': '#F79868', '2': '#F36B28' }

for row in df.itertuples():
    data.loc[row.Index, 'burn_style'] = burn_colors[row.burned]
    data.loc[row.Index, 'burn_opacity'] = 0.7 if row.burned != '' else 0

    data.loc[row.Index, 'published_style'] = publish_colors[row.published]
    data.loc[row.Index, 'published_opacity'] = 0.7 if row.published != '' else 0

    data.loc[row.Index, 'april_style'] = april_colors[row.court_count1]
    data.loc[row.Index, 'april_opacity'] = 0.7 if row.court_count1 != '' else 0

    data.loc[row.Index, 'may_style'] = may_colors[row.court_count_2]
    data.loc[row.Index, 'may_opacity'] = 0.7 if row.court_count_2 != '' else 0


data.head()

ID     county burned published court_count1 court_count_2  \
0   vas_accomack   Accomack      0         2                          1   
1  vas_albemarle  Albemarle      1         1                              
2     vas_amelia     Amelia      0         2                          1   
3    vas_amherst    Amherst      0                                    1   
4    vas_augusta    Augusta      0                                    1   

    fullName                                             change  \
0   ACCOMACK          [1663] ACCOMACK created from NORTHAMPTON.   
1  ALBEMARLE  ALBEMARLE gained from LOUISA, lost to creation...   
2     AMELIA          AMELIA lost to creation of PRINCE EDWARD.   
3    AMHERST                    AMHERST created from ALBEMARLE.   
4    AUGUSTA  AUGUSTA lost to creation of West Augusta Distr...   

                                               dates  \
0  {'start': '1663-12-31T00:00:00Z', 'end': '1776...   
1  {'start': '1761-05-01T00:00:00Z', 'end': '1776...   
2  {'start': '1754-01-01T00:00:00Z', 'end': '1776...   
3  {'start': '1761-05-01T00:00:00Z', 'end': '1776...   
4  {'start': '1773-10-11T00:00:00Z', 'end': '1776...   

                                            geometry burn_style  burn_opacity  \
0  MULTIPOLYGON (((-75.81141 37.79399, -75.81149 ...    #dddddd           0.7   
1  MULTIPOLYGON (((-78.58292 38.25014, -78.36980 ...    #cc0024           0.7   
2  MULTIPOLYGON (((-77.96820 37.48573, -77.95902 ...    #dddddd           0.7   
3  MULTIPOLYGON (((-78.83921 38.04757, -78.69671 ...    #dddddd           0.7   
4  MULTIPOLYGON (((-79.92785 39.58906, -79.91059 ...    #dddddd           0.7   

  published_style  published_opacity april_style  april_opacity  may_style  \
0         #016eae                0.7   #00000000            0.0    #F79868   
1         #7bb3d1                0.7   #00000000            0.0  #00000000   
2         #016eae                0.7   #00000000            0.0    #F79868   
3       #00000000                0.0   #00000000            0.0    #F79868   
4       #00000000                0.0   #00000000            0.0    #F79868   

   may_opacity  
0          0.7  
1          0.0  
2          0.7  
3          0.7  
4          0.7

# Split Layers

This splits each of the rows in the Excel sheet into its own layer. This is necessary because we want to be able to display each layer individually.

In [297]:
burned_layer = data.filter(['ID', 'burned', 'geometry', 'fullName', 'burn_style', 'burn_opacity']).copy().rename(columns={'burn_style': "fillColor", 'burn_opacity': 'opacity'})
burned_layer['burned'] = pd.to_numeric(burned_layer['burned'])

published_layer = data.filter(['ID', 'published', 'geometry', 'fullName', 'published_style', 'published_opacity']).copy().rename(columns={'published_style': "fillColor", 'published_opacity': 'opacity'})
published_layer['published'] = pd.to_numeric(published_layer['published'])

april_layer = data.filter(['ID', 'court_count1', 'geometry', 'fullName', 'april_style', 'april_opacity']).copy().rename(columns={'april_style': "fillColor", 'april_opacity': 'opacity'})
april_layer['court_count1'] = pd.to_numeric(april_layer['court_count1'])

may_layer = data.filter(['ID', 'court_count_2', 'geometry', 'fullName', 'may_style', 'may_opacity']).copy().rename(columns={'may_style':"fillColor", 'may_opacity': 'opacity'})
may_layer['court_count_2'] = pd.to_numeric(may_layer['court_count_2'])

# burned_layer.head()

# filtered_df.head()
may_layer.head()


ID  court_count_2  \
0   vas_accomack            1.0   
1  vas_albemarle            NaN   
2     vas_amelia            1.0   
3    vas_amherst            1.0   
4    vas_augusta            1.0   

                                            geometry   fullName  fillColor  \
0  MULTIPOLYGON (((-75.81141 37.79399, -75.81149 ...   ACCOMACK    #F79868   
1  MULTIPOLYGON (((-78.58292 38.25014, -78.36980 ...  ALBEMARLE  #00000000   
2  MULTIPOLYGON (((-77.96820 37.48573, -77.95902 ...     AMELIA    #F79868   
3  MULTIPOLYGON (((-78.83921 38.04757, -78.69671 ...    AMHERST    #F79868   
4  MULTIPOLYGON (((-79.92785 39.58906, -79.91059 ...    AUGUSTA    #F79868   

   opacity  
0      0.7  
1      0.0  
2      0.7  
3      0.7  
4      0.7

In [298]:
# burned_layer['burned'] = burned_layer.to_numeric(burned_layer['burned'], downcast='integer', errors='coerce')



# Mapping

Set up the folium map and add set the center an add the basemaps.

In [299]:
import folium

# remove labels from basemap
attr = (
    '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> '
    'contributors, &copy; <a href="https://cartodb.com/attributions">CartoDB</a>'
)
tiles = "https://{s}.basemaps.cartocdn.com/light_nolabels/{z}/{x}/{y}.png"

# calculate centroid to look at
centroid = [
    sum(data.geometry.total_bounds[[1, 3]]) / 2,
    sum(data.geometry.total_bounds[[0, 2]]) / 2
]

print(f"Data centroid: {centroid}")

m = folium.Map(centroid, attr="attr", zoom_start=7, control_scale=True)

folium.TileLayer(
    tiles=tiles,
    name='CartoDB Baselayer',
    attr=attr,
).add_to(m)

Data centroid: [38.6562172417811, -82.4068916037177]


## Layer Groups

Create layergroups for the map to allow users to turn information on/off.

In [300]:
counties_fg = folium.FeatureGroup(name="1774 Counties").add_to(m)
burned_fg = folium.FeatureGroup(name="Orders Burned for 1774").add_to(m)
published_fg = folium.FeatureGroup(name="Published resolves in Va. Gazette").add_to(m)
april_fg = folium.FeatureGroup(name="County court met, business from April 12-30").add_to(m)
may_fg = folium.FeatureGroup(name="County court met, business from May 1-31").add_to(m)

## Popups

In [301]:
def addPopup(fields = [], aliases = []):
    return folium.GeoJsonPopup(
        fields=fields,
        aliases=aliases,
        localized=True,
        labels=True,
        # style="background-color: yellow;"
    )

burned_popup = addPopup(['fullName', 'burned'], ["County Name", "Orders burned for 1774"])
published_popup = addPopup(['fullName', 'published'], ["County Name", "Published resolves in Va. Gazette"])
april_popup = addPopup(['fullName', 'court_count1'], ["County Name", "County court met, business from April 12-30"])
may_popup = addPopup(['fullName', 'court_count_2'], ["County Name", "County court met, business from May 1-31"])

In [302]:
april_layer.head()

ID  court_count1  \
0   vas_accomack           NaN   
1  vas_albemarle           NaN   
2     vas_amelia           NaN   
3    vas_amherst           NaN   
4    vas_augusta           NaN   

                                            geometry   fullName  fillColor  \
0  MULTIPOLYGON (((-75.81141 37.79399, -75.81149 ...   ACCOMACK  #00000000   
1  MULTIPOLYGON (((-78.58292 38.25014, -78.36980 ...  ALBEMARLE  #00000000   
2  MULTIPOLYGON (((-77.96820 37.48573, -77.95902 ...     AMELIA  #00000000   
3  MULTIPOLYGON (((-78.83921 38.04757, -78.69671 ...    AMHERST  #00000000   
4  MULTIPOLYGON (((-79.92785 39.58906, -79.91059 ...    AUGUSTA  #00000000   

   opacity  
0      0.0  
1      0.0  
2      0.0  
3      0.0  
4      0.0

Add layers to LayerGroups

In [303]:
# https://stackoverflow.com/questions/57314597/folium-choropleth-map-is-there-a-way-to-add-crosshatching-for-nan-values
# https://python-visualization.github.io/folium/latest/user_guide/plugins/pattern.html
from folium.plugins import StripePattern
from traitlets import default

# sp = StripePattern(angle=45, color='grey', space_color='white')
stripes = folium.plugins.StripePattern(angle=90, color='grey', space_color='white')
stripes2 = folium.plugins.StripePattern(angle=-45, color='grey', space_color='white')

# https://github.com/python-visualization/folium/blob/main/folium/plugins/pattern.py#L79
circles = folium.plugins.pattern.CirclePattern(
    fill_color='grey',
    color='grey', width=20, height=20, radius=5, fill_opacity=0.5, opacity=1
)

def published_style_function(feature): 
    default_style = {
        # "opacity": 0.4,
        "fillColor": "#00000000",
        "color": "black",
        "weight": 2
    }

    if  feature["properties"]["published"] == 2.0:
        default_style["fillPattern"] = circles
        default_style["fillOpacity"] = 0.7

    if  feature["properties"]["published"] == 1.0:
        default_style["fillPattern"] = stripes
        default_style["fillOpacity"] = 0.7

    return default_style

def burn_style_function(feature):
    default_style = {
        # "opacity": 1.0,
        # "fillColor": feature["properties"]["fillOpacity"],
        "fillColor": "#00000000",
        "color": "black",
        "weight": 0.4,
    }

    if feature["properties"]["burned"] == 1.0:
        # print(feature["properties"]["burned"])
        default_style["fillPattern"] = stripes2
        default_style["fillOpacity"] = 1.0

    return default_style

def style_function(feature):
    default_style = {
        "opacity": 1.0,
        #"fillColor": feature["properties"]["fillOpacity"],
        "fillColor": "#00000000",
        "color": "black",
        "weight": 0.4,
    }

    return default_style


In [304]:
april_layer.loc[[5]]

ID  court_count1  \
5  vas_bedford           1.0   

                                            geometry fullName fillColor  \
5  MULTIPOLYGON (((-79.43516 37.60388, -79.42851 ...  BEDFORD   #74D0F2   

   opacity  
5      0.7

In [305]:
folium.GeoJson(
    data,
    style_function=lambda x: {
        "fillColor": "#00000000",
        "color": "black"
    }
).add_to(counties_fg)

folium.GeoJson(
    burned_layer,
    smooth_factor=0.5,
    style_function=burn_style_function,
    popup=burned_popup,
).add_to(burned_fg)

# folium.GeoJson(
#     burned_layer,
#     style_function=lambda x: {
#         "fillColor": x['properties']['fillColor'],
#         "color": "black",
#         "fillOpacity": x['properties']['opacity'],
#         "fillPattern": stripes2,
#         "weight": 2
#     },
#     popup=burned_popup
# ).add_to(burned_fg)

folium.GeoJson(
    published_layer,
    style_function=published_style_function,
    # style_function=lambda x: {
    #     "fillColor": x['properties']['fillColor'],
    #     "color": "black",
    #     "fillOpacity": x['properties']['opacity']
    # },
    popup=published_popup
).add_to(published_fg)

folium.GeoJson(
    april_layer,
    style_function=lambda x: {
        "fillColor": x['properties']['fillColor'],
        "color": "black",
        "fillOpacity": x['properties']['opacity']
    },
    popup=april_popup
).add_to(april_fg)

folium.GeoJson(
    may_layer,
    style_function=lambda x: {
        "fillColor": x['properties']['fillColor'],
        "color": "black",
        # "fillOpacity": 0.4
        "fillOpacity": x['properties']['opacity']
    },
    popup=may_popup
).add_to(may_fg)

In [306]:
# https://gist.github.com/ColinTalbert/18f8901fc98f109f2b71156cf3ac81cd

from branca.element import Template, MacroElement

tempate = """
{% macro html(this, kwargs) %}
<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>1774 Virginia Court Actions</title>
  <link rel="stylesheet" href="https://code.jquery.com/ui/1.13.3/themes/base/jquery-ui.min.css">

  <script src="https://code.jquery.com/ui/1.13.3/jquery-ui.min.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});

  </script>
</head>
<body>

 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Legend (draggable)</div>
<div class='legend-scale'>
  <ul class='legend-labels'>

  <!-- 'Orders Not Burned': 'dddddd',
    'Orders Burned': 'cc0024', 
    'Resolves Not Published': 'dddddd',
    'Resolves Published': '7bb3d1',
    'Resolves Listed (not printed)': '016eae', 
    'County Court Did Not Meet (April)': 'F0DCDA',
    'County Court  Met (April)': 'E6B8B8',
    'County Court Scheduled, no meeting (April)': 'DA9695',
    'County Court Met (May)': 'D4D6DC',
    'County Court Did Not Meet (May)': 'C3CCD7',
    'County Court Scheduled, no meeting (May)': 'A0B5D2' 

   april_colors = { '': '#00000000', '0': '#FEF1E4', '1': '#74D0F2', '2': '#0BABD9' }
    may_colors = { '': '#00000000', '0': '#FEF1E4', '1': '#F79868', '2': '#F36B28' }

    
    'County Court Did Not Meet (April)': 'FEF1E4',
    'County Court  Met (April)': '74D0F2',
    'County Court Scheduled, no meeting (April)': '0BABD9',
    'County Court Met (May)': 'FEF1E4',
    'County Court Did Not Meet (May)': 'F79868',
    'County Court Scheduled, no meeting (May)': 'F36B28'
    

    <li><span style='background:#dddddd;opacity:0.4;'></span>Resolves Not Published</li>
    <li><span style='background:#7bb3d1;opacity:0.4;'></span>Resolves Published</li>
    <li><span style='background:#016eae;opacity:0.4;'></span>Resolves Listed (not printed)</li>-->
    <!-- https://stripesgenerator.com/ -->
    <li><span style='background-image: linear-gradient(45deg, #dddddd 8.33%, #ffffff 8.33%, #ffffff 50%, #dddddd 50%, #dddddd 58.33%, #ffffff 58.33%, #ffffff 100%);
background-size: 33.94px 33.94px;'></span>Resolves Not Published</li>
    <li><span style='background-image: linear-gradient(90deg, #dddddd 8.33%, #ffffff 8.33%, #ffffff 50%, #dddddd 50%, #dddddd 58.33%, #ffffff 58.33%, #ffffff 100%);
background-size: 48.00px 48.00px;'></span>Resolves Published</li>

    <li><span style='background-color: #e5e5f7;opacity: 1;background-image: radial-gradient(#cccccc 5px, #e5e5f7 2px);background-size: 10px 10px;'></span>Resolves Listed (not printed)</li>
    
    <li><span style='background:#FEF1E4;opacity:0.7;'></span>County Court Did Not Meet (April)</li>
    <li><span style='background:#74D0F2;opacity:0.7;'></span>County Court  Met (April)</li>
    <li><span style='background:#0BABD9;opacity:0.7;'></span>County Court Scheduled, no meeting (April)</li>

    <li><span style='background:#FEF1E4;opacity:0.7;'></span>County Court Did Not Meet (May)</li>
    <li><span style='background:#F79868;opacity:0.7;'></span>County Court  Met (May)</li>
    <li><span style='background:#F36B28;opacity:0.7;'></span>County Court Scheduled, no meeting (May)</li>

  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(tempate)
m.get_root().add_child(macro)

Show the map

In [307]:
folium.LayerControl().add_to(m)
m

In [308]:
m.save('docs/index.html')